In [ ]:
import pandas as pd
import requests
import numpy as np
from math import floor
from termcolor import colored as cl
import finnhub
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
import mplfinance as mpf
from mplfinance.original_flavor import candlestick_ohlc
import matplotlib.dates as mpl_dates
import seaborn as sns
from datetime import datetime

def get_all_trading_signal(ticker1, ticker2, ticker3):

#strategy1  = strategy1.drop('REGI')  
    def get_data(ticker):
        #ticker = 'ABBV'
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=6)
        end = today.strftime('%Y-%m-%d') 
        start = (today - delta).strftime('%Y-%m-%d')
     
        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volumn'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        
 
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        
        tick = ticker
        last_day.index = [tick]
        last_day['stop_loss'] = (last_day['vol_down2'] +last_day['vol_down3'] )/2
        last_day['stop_loss_pct'] = (last_day['Close']- last_day['stop_loss'])/last_day['Close']*100
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] +last_day['vol_down2'][-1] )/2            
        return last_day
    
    def get_signal(ticker):
        print(ticker)    
        from datetime import datetime as dt
        import datetime
        today = datetime.datetime.today()
        end =today.strftime('%Y-%m-%d') 
        start = (today-datetime.timedelta(200)).strftime('%Y-%m-%d') 

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        data1 = stock.copy()
         # strategy CALCULATION 
        def get_tsi(Close, long, short, signal):
            diff = Close - Close.shift(1)
            abs_diff = abs(diff)          
            diff_smoothed = diff.ewm(span = long, adjust = False).mean()
            diff_double_smoothed = diff_smoothed.ewm(span = short, adjust = False).mean()
            abs_diff_smoothed = abs_diff.ewm(span = long, adjust = False).mean()
            abs_diff_double_smoothed = abs_diff_smoothed.ewm(span = short, adjust = False).mean()
            
            tsi = (diff_double_smoothed / abs_diff_double_smoothed) * 100
            signal = tsi.ewm(span = signal, adjust = False).mean()       
            return tsi, signal
        data1['tsi'], data1['signal_line'] = get_tsi(data1['Close'], 25, 13, 12)
    
   
        def implement_tsi_strategy(prices, tsi, signal_line):
            buy_price = []
            sell_price = []
            tsi_signal = []
            signal = 0
            
            for i in range(len(prices)):
                if tsi[i-1] < signal_line[i-1] and tsi[i] > signal_line[i]:
                    if signal != 1:
                        buy_price.append(prices[i])
                        sell_price.append(np.nan)
                        signal = 1
                        tsi_signal.append(signal)
                    else:
                        buy_price.append(np.nan)
                        sell_price.append(np.nan)
                        tsi_signal.append(0)
                elif tsi[i-1] > signal_line[i-1] and tsi[i] < signal_line[i]:
                    if signal != -1:
                        buy_price.append(np.nan)
                        sell_price.append(prices[i])
                        signal = -1
                        tsi_signal.append(signal)
                    else:
                        buy_price.append(np.nan)
                        sell_price.append(np.nan)
                        tsi_signal.append(0)
                else:
                    buy_price.append(np.nan)
                    sell_price.append(np.nan)
                    tsi_signal.append(0)
                    
            return buy_price, sell_price, tsi_signal
        
        buy_price, sell_price, tsi_signal = implement_tsi_strategy(data1['Close'], data1['tsi'], data1['signal_line'])
    
        stop_loss_data =  get_data(ticker)
        d =stop_loss_data.loc[ticker,'stop_loss']         
        stock = stock.iloc[-15:,:]
        data = stock.copy()
        def ema(n, close):
            return close.ewm(span = n).mean()
        data['ema8'] = ema(8, data.Close)
        data['ema21'] = ema(21, data.Close)
        data['ema50'] = ema(50, data.Close)
        data['vol10'] = data['volume'].rolling(window = 10).mean()
        
        data3 = stock.copy()
        data3 =data3.reset_index()
        vup = []
        vup.append(data3.loc[0, 'Date'])
        vdown = []
        for i in range(1, len(data3)):
            if data3.loc[i, 'Close'] >= data3.loc[i-1, 'Close']:
                vup.append(data3.loc[i, 'Date'])
            if data3.loc[i, 'Close'] < data3.loc[i-1, 'Close']:
                vdown.append(data3.loc[i, 'Date'])
    
        plt.rcParams['axes.xmargin'] = 0
        plt.rcParams['figure.figsize'] = (15, 10)
        fig, axs = plt.subplots(2, gridspec_kw={'height_ratios': [7, 2]}, sharex=True)
       
        fig.patch.set_facecolor('white')  
        data['Date'] = pd.to_datetime(data.index)
        data['Date'] = data['Date'].apply(mpl_dates.date2num)
    
        data_plot = data.loc[:,['Date', 'Open', 'High', 'Low', 'Close']]
        candlestick_ohlc(axs[0], data_plot.values, width = 0.4,alpha = 1,
                        colorup = 'green', colordown = 'red')    
        data =data.set_index('Date')
        vup = mpl_dates.date2num(vup)
        vdown = mpl_dates.date2num(vdown)
        axs[1].bar(x = vup, height = data.loc[vup, 'volume'], color = 'green', width = 0.4)
        axs[1].bar(x = vdown, height = data.loc[vdown, 'volume'], color = 'red', width = 0.4)
        data['vol10'].plot(ax = axs[1], label = 'Avg_10days', color = 'steelblue', linewidth = 1)
        axs[1].ticklabel_format(useOffset=False, style='plain', axis='y')       
       
        c = buy_price[-1]
        c_an = c+c*0.01
        g = data.index[-1]+3
        axs[0].annotate('Buy: $'+ str(round(c,2)),size=24, xy = (data.index[-1], c),\
                  xycoords = 'data', xytext = (g, c_an),\
                  bbox = dict(boxstyle = 'round', 
                              fc = 'none', edgecolor='green',pad = 0.5),\
                  textcoords = 'data', arrowprops = dict(arrowstyle = '->',\
                                                         connectionstyle = 'arc3',lw =3, color = 'black'))
        f =  data.index[-1] +2
       # l_an = d-d*0.01
        if d<50:
            l_an = d-2
        elif 50<d<100:
            l_an = d-4
        elif 100 < d <= 200:
            l_an = d-6
        elif 200 < d <= 400:
            l_an = d-8
        elif d> 400:
            l_an = d-8
        axs[0].annotate("Stop: $" + str(round(d,2)), size = 24,xy = (data.index[-1], d),\
                  xycoords = 'data', xytext = (f, l_an),\
                  bbox = dict(boxstyle = 'round', fc = 'none',edgecolor='green', pad = 0.5),\
                  textcoords = 'data', arrowprops = dict(arrowstyle = '->',\
                    connectionstyle = 'arc3', lw =3,color = 'black'))
            
        axs[0].set_facecolor('white')
        axs[1].set_facecolor('white')
        axs[0].grid(b=True, which='major', color='grey', linestyle='--',alpha=0.8)
        #axs[0].grid(grid_visible=True, which='major', color='grey', linestyle='--', alpha=0.8)
        axs[1].grid(b=True, which='major', color='grey', linestyle='--',alpha=0.8)
        axs[0].set_xlim(min(data.index), max(data.index) + 8)
        axs[1].set_xlim(min(data.index) - 1, max(data.index) + 8)
      #  axs[0].set_ylim(min(data.Low)-15, max(data.High) + 8)
        date_format = mpl_dates.DateFormatter('%d %b %Y')
        axs[0].xaxis.set_major_formatter(date_format)
        axs[1].xaxis.set_major_formatter(date_format)
        axs[0].yaxis.tick_right()
        axs[1].yaxis.tick_right()
        axs[0].set(xlabel = '', ylabel = 'Price')
        axs[1].set(ylabel = 'Volume')
        axs[0].spines["bottom"].set_visible(True)
        axs[1].spines["top"].set_visible(True)
      #  axs[0].legend(loc = 'upper left')
        axs[1].legend(loc = 'upper left')
        axs[0].set_axisbelow(False)
        if buy_price[-1] < 120:
            axs[0].set_ylim(min(data.Low)-5, max(data.High) + 5)
            
        elif buy_price[-1] >120:
            axs[0].set_ylim(min(data.Low)-15, max(data.High) + 8)
        plt.subplots_adjust(hspace=0.1)
                           
       # g =data.index.tolist()[-1]
        plt.xticks(list(np.arange(min(data.index), max(data.index) + 1, 20)))
        axs[0].set_title(ticker+ " Trading Signal-GreenLine ", size = 14)
        path ="C:\\users\jizha\Desktop\seabridge fintech\image_trading_signal_green\\"
        plt.savefig(path +'{}.jpg'.format(ticker+"_Signal"), dpi = 25,pad_inches = 0,transparent=True)
        plt.show()    
        
    for ticker in ticker1:
        print(ticker)
        strategy1 = get_signal( ticker)
        
    
    image_trading_signal_green = pd.DataFrame()
    for ticker in ticker1:
        image = pd.DataFrame()
        dr = "https://3arbzfbsh-cname-us.ngrok.io/Desktop/seabridge%20fintech/image_trading_signal_green/" + ticker + "_Signal.jpg"
        tick = ticker
        image['image_Trading_signal'] =[ dr]
        image.index =[tick]
        image_trading_signal_green = pd.concat([image_trading_signal_green,image], axis =0)
            
    ############################second strategy#####################
    def get_signal2(ticker):
        print(ticker)
        from datetime import datetime as dt
        import datetime
        today = datetime.datetime.today()
        end =today.strftime('%Y-%m-%d') 
        start = (today-datetime.timedelta(200)).strftime('%Y-%m-%d') 
 
        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        data2 =stock.copy()
        
        